In [1]:
import numpy as np
import pandas as pd
import pandas_profiling
from sklearn import preprocessing
from sklearn.impute import SimpleImputer
from sklearn.model_selection import train_test_split

In [60]:
data = pd.read_csv("LifeEventPrediction-analytics-project/assets/data_asset/census_probabilities.csv")
data.shape

(1310400, 11)

In [3]:
from pandas_profiling import ProfileReport
profile = ProfileReport(data, title="Pandas Profiling Report")
profile.to_notebook_iframe()

# Handle Null Values

In [126]:
def process_na(df, na_values, threshold = 0.1, step_increase = 0.1):
    # if one row's na's are ALWAYS or almost always na in other rows, drop those rows
    # if a column  contains enough nas, then we see if we can drop those rows containing nas 
    for na_value in na_values:
        df = df.replace(na_value, np.nan)
    na_ratios = (df.isna().sum()/df.shape[0]).sort_values(ascending = False)
    na_ratios = na_ratios[na_ratios > threshold/100]
    for col in na_ratios.index:
        # for each column containing na values
        if na_ratios[col] > threshold:
            # if we can drop any row with na in that column, how does it affect other nas
            test = df.dropna(axis = 0, how = 'any', subset = [col])
            test_na_ratios = (test.isna().sum()/df.shape[0]).sort_values(ascending = False)
            test_na_ratios = test_na_ratios[test_na_ratios > threshold/100]
            # if the new na ratios have decreased significantly across other colmns, its a good drop
            if np.any(((na_ratios - test_na_ratios) - step_increase) < 0):
                # successful drops
                df = test
    return df

In [144]:
def prep_discrete(cols):
    return cols

def prep_continuous(cols, norm = True):
    """
    col: a 2-D array of all numerical values
    """
    numerical_imputer = SimpleImputer(missing_values = np.nan, strategy = "mean")
    cols = numerical_imputer.fit_transform(cols)
    if norm:
        return preprocessing.normalize(cols)
    else:
        return cols

def prep_char(cols, expected_length = 1):
    if how == "":
        return 
    return col

def prep_categorical(cols):
    categorical_imputer = SimpleImputer(missing_values = np.nan, strategy = "most_frequent")
    le = preprocessing.LabelEncoder()
    imputed = categorical_imputer.fit_transform(cols).T
    for col in range(imputed.shape[0]):
        imputed[col] = le.fit_transform(imputed[col])
    return imputed.T

def prep_all(df, na_values = ["Unknown"]):
    df = process_na(df, na_values)
    int_cols = df.dtypes[df.dtypes == "int"]
    float_cols = df.dtypes[df.dtypes == "float"]
    cat_cols = df.dtypes[(df.dtypes == "object") | (df.dtypes == "string")]
    encoded_categorical = prep_categorical(df[cat_cols.index])
    encoded_continuous = prep_continuous(df[float_cols.index])
    
    #merge all outputs
    return encoded_categorical, encoded_continuous

In [145]:
prep_all(data)

(array([[4, 1, 1, ..., 1, 0, 0],
        [4, 1, 1, ..., 0, 3, 2],
        [4, 1, 1, ..., 1, 3, 6],
        ...,
        [50, 0, 3, ..., 0, 3, 6],
        [50, 0, 3, ..., 1, 4, 7],
        [50, 2, 2, ..., 0, 4, 1]], dtype=object),
 array([[0.        , 0.        , 0.        , 0.        ],
        [0.84512653, 0.52832427, 0.        , 0.08145311],
        [0.99925948, 0.        , 0.        , 0.03847706],
        ...,
        [0.        , 0.        , 0.        , 0.        ],
        [0.        , 0.        , 0.        , 0.        ],
        [0.        , 0.        , 1.        , 0.        ]]))